# 3-6. 予測・判断 - MSE（Mean Square Error）、特徴量の効果的な選択
3-4.や3-6.で扱ってきた正解率や適合率などの指標は分類モデルの評価指標であったが，回帰モデル（すなわち，カテゴリではなく数値として予測が行えるモデル）に対してはMSE（Mean Square Error，平均二乗誤差）という評価指標が存在する．

ここでは「週刊少年ジャンプのページ数・価格・公開年月日から消費者物価指数（書籍）を予測する回帰モデル」と，「なんの関連もないデータを使って学習した同様の予測器」のMSEを比べることでモデルの精度を比較してみよう．

週刊少年ジャンプのデータについては3-4. 畳み込みニューラルネットワーク（CNN）/再帰型ニューラルネットワーク（RNN）のデータと同様のものを扱う．持っていない場合は以下のコードを[SPARQLクエリサービス](https://mediag.bunka.go.jp/madb_lab/lod/sparql/)上に入力して実行する，または入力を省略した[こちらのURL](https://mediag.bunka.go.jp/madb_lab/lod/sparql/#query=PREFIX%20rdfs%3A%20%20%20%3Chttp%3A%2F%2Fwww.w3.org%2F2000%2F01%2Frdf-schema%23%3E%0APREFIX%20schema%3A%20%3Chttps%3A%2F%2Fschema.org%2F%3E%20SELECT%20%3F%E3%83%A9%E3%83%99%E3%83%AB%20%3F%E5%85%AC%E9%96%8B%E5%B9%B4%E6%9C%88%E6%97%A5%20%3F%E4%BE%A1%E6%A0%BC%20%3F%E3%83%9A%E3%83%BC%E3%82%B8%0AWHERE%20%7B%0A%20%20%3F%E3%82%A2%E3%82%A4%E3%83%86%E3%83%A0%0A%20%20%20%20%20%20%20%20schema%3Agenre%20%22%E3%83%9E%E3%83%B3%E3%82%AC%E9%9B%91%E8%AA%8C%E5%8D%98%E5%8F%B7%22%3B%0A%20%20%20%20%20%20%20%20schema%3Aname%20%22%E9%80%B1%E5%88%8A%E5%B0%91%E5%B9%B4%E3%82%B8%E3%83%A3%E3%83%B3%E3%83%97%22%3B%0A%20%20%20%20%20%20%20%20rdfs%3Alabel%20%3F%E3%83%A9%E3%83%99%E3%83%AB%3B%0A%20%20%20%20%20%20%20%20schema%3Aprice%20%3F%E4%BE%A1%E6%A0%BC%3B%0A%20%20%20%20%20%20%20%20schema%3AnumberOfPages%20%3F%E3%83%9A%E3%83%BC%E3%82%B8%3B%0A%20%20%20%20%20%20%20%20schema%3AdatePublished%20%3F%E5%85%AC%E9%96%8B%E5%B9%B4%E6%9C%88%E6%97%A5.%0A%7D&endpoint=https%3A%2F%2Fmediag.bunka.go.jp%2Fsparql&requestMethod=POST&tabTitle=Query&headers=%7B%7D&contentTypeConstruct=application%2Fn-triples%2C*%2F*%3Bq%3D0.9&contentTypeSelect=application%2Fsparql-results%2Bjson%2C*%2F*%3Bq%3D0.9&outputFormat=table)から実行してデータを取得できる．

取得したCSVファイルを「週刊少年ジャンプ.csv」として保存し，このノートブック上にアップロードしよう．

```
PREFIX rdfs:   <http://www.w3.org/2000/01/rdf-schema#>
PREFIX schema: <https://schema.org/> SELECT ?ラベル ?公開年月日 ?価格 ?ページ
WHERE {
  ?アイテム
        schema:genre "マンガ雑誌単号";
        schema:name "週刊少年ジャンプ";
        rdfs:label ?ラベル;
        schema:price ?価格;
        schema:numberOfPages ?ページ;
        schema:datePublished ?公開年月日.
}
```

消費者物価指数（書籍）は[政府統計の総合窓口e-statのDB](https://www.e-stat.go.jp/dbview?sid=0003427113)上で情報を絞ってダウンロードしてくることができる．整形済みのものを用意したので，[こちら](https://mediag.bunka.go.jp/madb_lab/wp-content/themes/madb_lab/files/usecase3/3_6_02.csv)から取得し，「消費者物価指数_全国_書籍.csv」としてアップロードしよう．

## データの整形

In [ ]:
# 必要なモジュールの読み込み
import pandas as pd
import numpy as np
import re
import datetime as dt
from sklearn.preprocessing import StandardScaler

In [ ]:
# ジャンプのデータ（説明変数）
jumps = pd.read_csv("/content/週刊少年ジャンプ.csv")
jumps = jumps.drop_duplicates().reset_index(drop=True)

jumps['公開年月日'] = pd.to_datetime(jumps['公開年月日'])
jumps.sort_values(by = '公開年月日', ascending = True, inplace = True)
jumps.reset_index(inplace=True, drop=True)

for i in jumps.index:
  price = re.sub(r"\D", "", jumps["価格"][i])
  if price != "":
    jumps["価格"][i] = int(price)
  else:
    jumps["価格"][i] = None

  page = re.sub(r"\D", "", jumps["ページ"][i])
  if page != "":
    jumps["ページ"][i] = int(page)
  else:
    jumps["ページ"][i] = None

jumps = jumps.dropna()
jumps.reset_index(inplace=True, drop=True)
jumps

<ipython-input-6-fa9a78688f98>:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  jumps["価格"][i] = int(price)
<ipython-input-6-fa9a78688f98>:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  jumps["ページ"][i] = int(page)
<ipython-input-6-fa9a78688f98>:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  jumps["価格"][i] = None


ラベル      公開年月日   価格  ページ
0     週刊少年ジャンプ 1969年 表示号数20 1969-11-03   90  296
1     週刊少年ジャンプ 1969年 表示号数21 1969-11-10   90  294
2     週刊少年ジャンプ 1969年 表示号数22 1969-11-17   90  312
3     週刊少年ジャンプ 1969年 表示号数23 1969-11-24   90  294
4     週刊少年ジャンプ 1969年 表示号数24 1969-12-01   90  294
...                     ...        ...  ...  ...
2379  週刊少年ジャンプ 2018年 表示号数24 2018-05-28  270  464
2380  週刊少年ジャンプ 2018年 表示号数25 2018-06-04  270  496
2381  週刊少年ジャンプ 2018年 表示号数26 2018-06-11  270  450
2382  週刊少年ジャンプ 2018年 表示号数27 2018-06-18  270  492
2383  週刊少年ジャンプ 2018年 表示号数28 2018-06-25  270  494

[2384 rows x 4 columns]

In [ ]:
jumps_month = pd.DataFrame(columns=["公開年", "公開月", "価格", "ページ"])
dates = []
# 月平均にする
for year in range(1970, 2016):
  for month in range(1,13):
    data = jumps[(jumps['公開年月日'] >= dt.datetime(year,month,1)) & (jumps['公開年月日'] < dt.datetime(year+month//12,(month)%12+1,1))][["公開年月日", "価格", "ページ"]]
    price_mean = sum(data["価格"])/len(data.index)
    page_mean = sum(data["ページ"])/len(data.index)
    dates.append(dt.datetime(year, month, 1))
    series = pd.Series([year, month, price_mean, page_mean])
    jumps_month = pd.concat([jumps_month, pd.DataFrame(series.values.reshape(1, -1), columns=jumps_month.columns)], axis=0)
jumps_month.index = dates
jumps_month

公開年   公開月      価格         ページ
1970-01-01  1970.0   1.0   90.00  327.333333
1970-02-01  1970.0   2.0   80.00  280.000000
1970-03-01  1970.0   3.0   82.00  282.400000
1970-04-01  1970.0   4.0   82.50  284.000000
1970-05-01  1970.0   5.0   82.50  284.000000
...            ...   ...     ...         ...
2015-08-01  2015.0   8.0  258.75  518.000000
2015-09-01  2015.0   9.0  255.00  492.000000
2015-10-01  2015.0  10.0  255.00  492.000000
2015-11-01  2015.0  11.0  255.00  488.400000
2015-12-01  2015.0  12.0  255.00  496.000000

[552 rows x 4 columns]

In [ ]:
# 消費者物価指数のデータ（目標変数）
cpis = pd.read_csv("/content/消費者物価指数_全国_書籍.csv", index_col=None).drop(columns=["地域（2020年基準）", "2020年基準品目", "/時間軸（年・月）", "表章項目"]).transpose()
new_columns = [["物価指数"]]
new_index = []
for idx in cpis.index:
  year_month = re.findall(r"\d+", idx)
  if int(year_month[0]) < 2016:
    new_index.append(dt.datetime(int(year_month[0]), int(year_month[1]), 1))
  else:
    cpis = cpis.drop([idx], axis=0)

cpis.index = new_index
cpis.columns = new_columns
cpis = cpis.sort_index()
cpis

物価指数
1970-01-01  17.9
1970-02-01  18.0
1970-03-01  18.0
1970-04-01  18.0
1970-05-01  18.0
...          ...
2015-08-01  94.3
2015-09-01  94.1
2015-10-01  94.3
2015-11-01  94.4
2015-12-01  94.4

[552 rows x 1 columns]

In [ ]:
# ランダムな（意味のない）説明変数データ
dummy = pd.DataFrame(np.random.randint(0, 100, cpis.shape[0]), index = cpis.index, columns=["ランダム"])
dummy

ランダム
1970-01-01     9
1970-02-01    86
1970-03-01    90
1970-04-01    60
1970-05-01    58
...          ...
2015-08-01     7
2015-09-01     2
2015-10-01    88
2015-11-01    29
2015-12-01    68

[552 rows x 1 columns]

In [ ]:
# 学習データとテストデータに分割
X_train = jumps_month[jumps_month.index < dt.datetime(2001,1,1)]
y_train = cpis[cpis.index < dt.datetime(2001,1,1)]
dummy_train = dummy[dummy.index < dt.datetime(2001,1,1)]

X_test = jumps_month[jumps_month.index > dt.datetime(2000,12,1)]
y_test = cpis[cpis.index > dt.datetime(2000,12,1)]
dummy_test = dummy[dummy.index > dt.datetime(2000,12,1)]

# 正規化
X_scaler = StandardScaler().fit(X_train)
X_train = X_scaler.transform(X_train)
X_test = X_scaler.transform(X_test)

dummy_scaler = StandardScaler().fit(dummy_train)
dummy_train = dummy_scaler.transform(dummy_train)
dummy_test = dummy_scaler.transform(dummy_test)

## モデルの作成

In [ ]:
# 必要なモジュールのインポート
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error

In [ ]:
# ジャンプのデータを使った予測モデルを作成
model = LinearRegression()
model.fit(X_train, y_train)

# ランダムデータを使った予測モデルを作成
model_dummy = LinearRegression()
model_dummy.fit(dummy_train, y_train)

LinearRegression()

## MSEによる評価

In [ ]:
# ジャンプのデータを使った予測モデルによるテストデータに対してのMSE
y_pred = model.predict(X_test)
mse = mean_squared_error(y_test, y_pred)

# ランダムデータを使った予測モデルによるテストデータに対してのMSE
dummy_pred = model_dummy.predict(dummy_test)
mse_dummy = mean_squared_error(dummy_test, dummy_pred)

print("ジャンプのデータによるモデルのMSE: ", mse)
print("ランダムデータによるモデルのMSE: ", mse_dummy)

ジャンプのデータによるモデルのMSE:  328.8185725695346
ランダムデータによるモデルのMSE:  3409.641159688738


以上の結果から，ジャンプのデータを利用して計算したモデル方が適当な値で計算したモデルよりも良い結果（＝小さい損失）であったという評価ができる．

# 3-6. 予測・判断 - 特徴量の効果的な選択
線形回帰モデルにおいては，L1正則化項を用いた損失関数を用いる手法（Lasso回帰）で特徴量を選択することもできる．

Pythonではscikit-learnにLassoライブラリが用意されており，それを利用することで簡単に次元削減することができる．

In [ ]:
from sklearn.linear_model import Lasso

In [ ]:
lasso = Lasso()

# 学習
lasso.fit(X_train, y_train)

# 予測
y_pred = lasso.predict(X_test)

# MSE
mse_lasso = mean_squared_error(y_test, y_pred)
print("ジャンプのデータによるLasso回帰モデルのMSE: ", mse_lasso)

# 重要度の確認
lasso.coef_


ジャンプのデータによるLasso回帰モデルのMSE:  222.4534878864677


array([12.94084538,  0.        ,  7.22576418,  0.        ])

MSEの値も通常の線形回帰モデルより小さく良い値になっている．
また，重要度を見るといくつかの値（公開月，ページ）の重要度が0になっていることがわかる．
このことから，公開年と価格の推移だけで十分な推測ができるということがわかる．